## POS Tagging - Lexicon and Rule Based Taggers

Let's look at the two most basic tagging techniques - lexicon based (or unigram) and rule-based. 

In this guided exercise, you will explore the WSJ (wall street journal) POS-tagged corpus that comes with NLTK and build a lexicon and rule-based tagger using this corpus as the tarining data. 

This exercise is divided into the following sections:
1. Reading and understanding the tagged dataset
2. Exploratory analysis

### 1. Reading and understanding the tagged dataset

In [2]:
# Importing libraries
import nltk
import numpy as np
import pandas as pd
import pprint, time
import random
from sklearn.model_selection import train_test_split
from nltk.tokenize import word_tokenize
import math

In [3]:
# reading the Treebank tagged sentences
wsj = list(nltk.corpus.treebank.tagged_sents())

In [8]:
test = list(nltk.corpus.treebank.sents())
test

[['Pierre',
  'Vinken',
  ',',
  '61',
  'years',
  'old',
  ',',
  'will',
  'join',
  'the',
  'board',
  'as',
  'a',
  'nonexecutive',
  'director',
  'Nov.',
  '29',
  '.'],
 ['Mr.',
  'Vinken',
  'is',
  'chairman',
  'of',
  'Elsevier',
  'N.V.',
  ',',
  'the',
  'Dutch',
  'publishing',
  'group',
  '.'],
 ['Rudolph',
  'Agnew',
  ',',
  '55',
  'years',
  'old',
  'and',
  'former',
  'chairman',
  'of',
  'Consolidated',
  'Gold',
  'Fields',
  'PLC',
  ',',
  'was',
  'named',
  '*-1',
  'a',
  'nonexecutive',
  'director',
  'of',
  'this',
  'British',
  'industrial',
  'conglomerate',
  '.'],
 ['A',
  'form',
  'of',
  'asbestos',
  'once',
  'used',
  '*',
  '*',
  'to',
  'make',
  'Kent',
  'cigarette',
  'filters',
  'has',
  'caused',
  'a',
  'high',
  'percentage',
  'of',
  'cancer',
  'deaths',
  'among',
  'a',
  'group',
  'of',
  'workers',
  'exposed',
  '*',
  'to',
  'it',
  'more',
  'than',
  '30',
  'years',
  'ago',
  ',',
  'researchers',
  'reported'

In [9]:
# samples: Each sentence is a list of (word, pos) tuples
wsj[:3]

[[('Pierre', 'NNP'),
  ('Vinken', 'NNP'),
  (',', ','),
  ('61', 'CD'),
  ('years', 'NNS'),
  ('old', 'JJ'),
  (',', ','),
  ('will', 'MD'),
  ('join', 'VB'),
  ('the', 'DT'),
  ('board', 'NN'),
  ('as', 'IN'),
  ('a', 'DT'),
  ('nonexecutive', 'JJ'),
  ('director', 'NN'),
  ('Nov.', 'NNP'),
  ('29', 'CD'),
  ('.', '.')],
 [('Mr.', 'NNP'),
  ('Vinken', 'NNP'),
  ('is', 'VBZ'),
  ('chairman', 'NN'),
  ('of', 'IN'),
  ('Elsevier', 'NNP'),
  ('N.V.', 'NNP'),
  (',', ','),
  ('the', 'DT'),
  ('Dutch', 'NNP'),
  ('publishing', 'VBG'),
  ('group', 'NN'),
  ('.', '.')],
 [('Rudolph', 'NNP'),
  ('Agnew', 'NNP'),
  (',', ','),
  ('55', 'CD'),
  ('years', 'NNS'),
  ('old', 'JJ'),
  ('and', 'CC'),
  ('former', 'JJ'),
  ('chairman', 'NN'),
  ('of', 'IN'),
  ('Consolidated', 'NNP'),
  ('Gold', 'NNP'),
  ('Fields', 'NNP'),
  ('PLC', 'NNP'),
  (',', ','),
  ('was', 'VBD'),
  ('named', 'VBN'),
  ('*-1', '-NONE-'),
  ('a', 'DT'),
  ('nonexecutive', 'JJ'),
  ('director', 'NN'),
  ('of', 'IN'),
  ('this'

In the list mentioned above, each element of the list is a sentence. Also, note that each sentence ends with a full stop '.' whose POS tag is also a '.'. Thus, the POS tag '.' demarcates the end of a sentence.

Also, we do not need the corpus to be segmented into sentences, but can rather use a list of (word, tag) tuples. Let's convert the list into a (word, tag) tuple.

In [10]:
# converting the list of sents to a list of (word, pos tag) tuples
tagged_words = [tup for sent in wsj for tup in sent]
print(len(tagged_words))
tagged_words[:10]

100676


[('Pierre', 'NNP'),
 ('Vinken', 'NNP'),
 (',', ','),
 ('61', 'CD'),
 ('years', 'NNS'),
 ('old', 'JJ'),
 (',', ','),
 ('will', 'MD'),
 ('join', 'VB'),
 ('the', 'DT')]

We now have a list of about 100676 (word, tag) tuples. Let's now do some exploratory analyses.

### 2. Exploratory Analysis

Let's now conduct some basic exploratory analysis to understand the tagged corpus. To start with, let's ask some simple questions:
1. How many unique tags are there in the corpus? 
2. Which is the most frequent tag in the corpus?
3. Which tag is most commonly assigned to the following words:
    - "bank"
    - "executive"


In [13]:
# question 1: Find the number of unique POS tags in the corpus
# you can use the set() function on the list of tags to get a unique set of tags, 
# and compute its length
tags = [pair[1] for pair in tagged_words]
unique_tags = set(tags)
len(unique_tags)

46

In [14]:
unique_tags

{'#',
 '$',
 "''",
 ',',
 '-LRB-',
 '-NONE-',
 '-RRB-',
 '.',
 ':',
 'CC',
 'CD',
 'DT',
 'EX',
 'FW',
 'IN',
 'JJ',
 'JJR',
 'JJS',
 'LS',
 'MD',
 'NN',
 'NNP',
 'NNPS',
 'NNS',
 'PDT',
 'POS',
 'PRP',
 'PRP$',
 'RB',
 'RBR',
 'RBS',
 'RP',
 'SYM',
 'TO',
 'UH',
 'VB',
 'VBD',
 'VBG',
 'VBN',
 'VBP',
 'VBZ',
 'WDT',
 'WP',
 'WP$',
 'WRB',
 '``'}

In [16]:
# question 2: Which is the most frequent tag in the corpus
# to count the frequency of elements in a list, the Counter() class from collections
# module is very useful, as shown below

from collections import Counter
tag_counts = Counter(tags)
tag_counts

Counter({'NNP': 9410,
         ',': 4886,
         'CD': 3546,
         'NNS': 6047,
         'JJ': 5834,
         'MD': 927,
         'VB': 2554,
         'DT': 8165,
         'NN': 13166,
         'IN': 9857,
         '.': 3874,
         'VBZ': 2125,
         'VBG': 1460,
         'CC': 2265,
         'VBD': 3043,
         'VBN': 2134,
         '-NONE-': 6592,
         'RB': 2822,
         'TO': 2179,
         'PRP': 1716,
         'RBR': 136,
         'WDT': 445,
         'VBP': 1321,
         'RP': 216,
         'PRP$': 766,
         'JJS': 182,
         'POS': 824,
         '``': 712,
         'EX': 88,
         "''": 694,
         'WP': 241,
         ':': 563,
         'JJR': 381,
         'WRB': 178,
         '$': 724,
         'NNPS': 244,
         'WP$': 14,
         '-LRB-': 120,
         '-RRB-': 126,
         'PDT': 27,
         'RBS': 35,
         'FW': 4,
         'UH': 3,
         'SYM': 1,
         'LS': 13,
         '#': 16})

In [17]:
# the most common tags can be seen using the most_common() method of Counter
tag_counts.most_common(5)

[('NN', 13166), ('IN', 9857), ('NNP', 9410), ('DT', 8165), ('-NONE-', 6592)]

Thus, NN is the most common tag followed by IN, NNP, DT, -NONE- etc. You can read the exhaustive list of tags using the NLTK documentation as shown below.

In [18]:
# list of POS tags in NLTK
nltk.help.upenn_tagset()

$: dollar
    $ -$ --$ A$ C$ HK$ M$ NZ$ S$ U.S.$ US$
'': closing quotation mark
    ' ''
(: opening parenthesis
    ( [ {
): closing parenthesis
    ) ] }
,: comma
    ,
--: dash
    --
.: sentence terminator
    . ! ?
:: colon or ellipsis
    : ; ...
CC: conjunction, coordinating
    & 'n and both but either et for less minus neither nor or plus so
    therefore times v. versus vs. whether yet
CD: numeral, cardinal
    mid-1890 nine-thirty forty-two one-tenth ten million 0.5 one forty-
    seven 1987 twenty '79 zero two 78-degrees eighty-four IX '60s .025
    fifteen 271,124 dozen quintillion DM2,000 ...
DT: determiner
    all an another any both del each either every half la many much nary
    neither no some such that the them these this those
EX: existential there
    there
FW: foreign word
    gemeinschaft hund ich jeux habeas Haementeria Herr K'ang-si vous
    lutihaw alai je jour objets salutaris fille quibusdam pas trop Monte
    terram fiche oui corporis ...
IN: preposition or

In [22]:
# question 3: Which tag is most commonly assigned to the word w. Get the tags list that appear for word w and then use the Counter()
# Try w ='bank' 
bank = Counter([pair for pair in tagged_words if(pair[0].lower() == 'bank')])
bank

Counter({('bank', 'NN'): 38, ('Bank', 'NNP'): 32})

In [25]:
# question 3: Which tag is most commonly assigned to the word w. Try 'executive' 
executive = Counter([pair for pair in tagged_words if(pair[0].lower() == 'executive')])
executive

Counter({('executive', 'NN'): 40, ('executive', 'JJ'): 28})

### 2. Exploratory Analysis Contd.

Until now, we were looking at the frequency of tags assigned to particular words, which is the basic idea used by lexicon or unigram taggers. Let's now try observing some rules which can potentially be used for POS tagging. 

To start with, let's see if the following questions reveal something useful:

4. What fraction of words with the tag 'VBD' (verb, past tense) end with the letters 'ed'
5. What fraction of words with the tag 'VBG' (verb, present participle/gerund) end with the letters 'ing'

In [28]:
# 4. how many words with the tag 'VBD' (verb, past tense) end with 'ed'
# first get the all the words tagged as VBD
past_tense_verbs = [pair for pair in tagged_words if(pair[1] == 'VBD')]

# subset the past tense verbs with words ending with 'ed'. (Try w.endswith('ed'))
ed_verbs = [test for test in past_tense_verbs  if test[0].endswith('ed')]
print(len(ed_verbs) / len(past_tense_verbs))
ed_verbs[:20]

0.3881038448899113


[('reported', 'VBD'),
 ('stopped', 'VBD'),
 ('studied', 'VBD'),
 ('led', 'VBD'),
 ('worked', 'VBD'),
 ('explained', 'VBD'),
 ('imposed', 'VBD'),
 ('dumped', 'VBD'),
 ('poured', 'VBD'),
 ('mixed', 'VBD'),
 ('described', 'VBD'),
 ('ventilated', 'VBD'),
 ('contracted', 'VBD'),
 ('continued', 'VBD'),
 ('eased', 'VBD'),
 ('ended', 'VBD'),
 ('lengthened', 'VBD'),
 ('reached', 'VBD'),
 ('resigned', 'VBD'),
 ('approved', 'VBD')]

In [29]:
# 5. how many words with the tag 'VBG' end with 'ing'
participle_verbs = [ pair for pair in tagged_words if(pair[1] == 'VBG')]
ing_verbs = [pair for pair in tagged_words if pair[0].endswith('ed') ]
print(len(ing_verbs) / len(participle_verbs))
ing_verbs[:20]

2.1904109589041094


[('Consolidated', 'NNP'),
 ('named', 'VBN'),
 ('used', 'VBN'),
 ('caused', 'VBN'),
 ('exposed', 'VBN'),
 ('reported', 'VBD'),
 ('York-based', 'JJ'),
 ('stopped', 'VBD'),
 ('reported', 'VBN'),
 ('studied', 'VBD'),
 ('led', 'VBD'),
 ('used', 'VBN'),
 ('replaced', 'VBN'),
 ('worked', 'VBD'),
 ('died', 'VBN'),
 ('expected', 'VBN'),
 ('asbestos-related', 'JJ'),
 ('diagnosed', 'VBN'),
 ('expected', 'VBN'),
 ('asbestos-related', 'JJ')]

## 2. Exploratory Analysis Continued

Let's now try observing some tag patterns using the fact the some tags are more likely to apper after certain other tags. For e.g. most nouns NN are usually followed by determiners DT ("The/DT constitution/NN"), adjectives JJ usually precede a noun NN (" A large/JJ building/NN"), etc. 

Try answering the following questions:
1. What fraction of adjectives JJ are followed by a noun NN? 
2. What fraction of determiners DT are followed by a noun NN?
3. What fraction of modals MD are followed by a verb VB?

In [39]:
tags = [pair[1] for pair in tagged_words]
jj_tags = [tag for tag in tags if tag == 'JJ']

for index, t in enumerate(tags):
   




index 0
t NNP
index 1
t NNP
index 2
t ,
index 3
t CD
index 4
t NNS
index 5
t JJ
index 6
t ,
index 7
t MD
index 8
t VB
index 9
t DT
index 10
t NN
index 11
t IN
index 12
t DT
index 13
t JJ
index 14
t NN
index 15
t NNP
index 16
t CD
index 17
t .
index 18
t NNP
index 19
t NNP
index 20
t VBZ
index 21
t NN
index 22
t IN
index 23
t NNP
index 24
t NNP
index 25
t ,
index 26
t DT
index 27
t NNP
index 28
t VBG
index 29
t NN
index 30
t .
index 31
t NNP
index 32
t NNP
index 33
t ,
index 34
t CD
index 35
t NNS
index 36
t JJ
index 37
t CC
index 38
t JJ
index 39
t NN
index 40
t IN
index 41
t NNP
index 42
t NNP
index 43
t NNP
index 44
t NNP
index 45
t ,
index 46
t VBD
index 47
t VBN
index 48
t -NONE-
index 49
t DT
index 50
t JJ
index 51
t NN
index 52
t IN
index 53
t DT
index 54
t JJ
index 55
t JJ
index 56
t NN
index 57
t .
index 58
t DT
index 59
t NN
index 60
t IN
index 61
t NN
index 62
t RB
index 63
t VBN
index 64
t -NONE-
index 65
t -NONE-
index 66
t TO
index 67
t VB
index 68
t NNP
index 69
t NN
inde

index 914
t .
index 915
t JJ
index 916
t NN
index 917
t IN
index 918
t DT
index 919
t NNS
index 920
t POS
index 921
t NNS
index 922
t VBD
index 923
t IN
index 924
t DT
index 925
t NN
index 926
t TO
index 927
t CD
index 928
t NNS
index 929
t ,
index 930
t DT
index 931
t JJS
index 932
t IN
index 933
t JJ
index 934
t NNP
index 935
t ,
index 936
t VBG
index 937
t TO
index 938
t NNP
index 939
t POS
index 940
t .
index 941
t JJR
index 942
t NNS
index 943
t VBP
index 944
t VBN
index 945
t -NONE-
index 946
t TO
index 947
t VB
index 948
t VBG
index 949
t NN
index 950
t NNS
index 951
t IN
index 952
t PRP
index 953
t VBP
index 954
t NN
index 955
t NNS
index 956
t TO
index 957
t VB
index 958
t RB
index 959
t JJR
index 960
t NNS
index 961
t IN
index 962
t DT
index 963
t JJR
index 964
t NN
index 965
t .
index 966
t JJR
index 967
t NNS
index 968
t VBP
index 969
t VBN
index 970
t -NONE-
index 971
t DT
index 972
t NN
index 973
t IN
index 974
t VBG
index 975
t NNS
index 976
t IN
index 977
t NN
index 978

t IN
index 1440
t NNP
index 1441
t VBZ
index 1442
t RB
index 1443
t VBN
index 1444
t DT
index 1445
t NN
index 1446
t IN
index 1447
t NN
index 1448
t NN
index 1449
t .
index 1450
t IN
index 1451
t NNP
index 1452
t VBZ
index 1453
t ,
index 1454
t DT
index 1455
t NN
index 1456
t VBZ
index 1457
t RB
index 1458
t DT
index 1459
t NN
index 1460
t -NONE-
index 1461
t TO
index 1462
t VB
index 1463
t JJ
index 1464
t NN
index 1465
t NNS
index 1466
t IN
index 1467
t DT
index 1468
t NN
index 1469
t ,
index 1470
t DT
index 1471
t NNP
index 1472
t VBD
index 1473
t -NONE-
index 1474
t -NONE-
index 1475
t .
index 1476
t DT
index 1477
t NN
index 1478
t POS
index 1479
t NN
index 1480
t NN
index 1481
t VBD
index 1482
t IN
index 1483
t NN
index 1484
t NNP
index 1485
t TO
index 1486
t $
index 1487
t CD
index 1488
t CD
index 1489
t -NONE-
index 1490
t IN
index 1491
t $
index 1492
t CD
index 1493
t CD
index 1494
t -NONE-
index 1495
t .
index 1496
t NN
index 1497
t -NONE-
index 1498
t -NONE-
index 1499
t TO
in

t IN
index 2078
t JJ
index 2079
t NNS
index 2080
t .
index 2081
t CC
index 2082
t IN
index 2083
t RB
index 2084
t ,
index 2085
t PRP
index 2086
t VBP
index 2087
t VBG
index 2088
t RB
index 2089
t TO
index 2090
t PRP$
index 2091
t NN
index 2092
t NN
index 2093
t :
index 2094
t NNP
index 2095
t IN
index 2096
t NNP
index 2097
t .
index 2098
t NNP
index 2099
t NNP
index 2100
t VBD
index 2101
t DT
index 2102
t NN
index 2103
t NN
index 2104
t IN
index 2105
t $
index 2106
t CD
index 2107
t CD
index 2108
t -NONE-
index 2109
t IN
index 2110
t NNP
index 2111
t ,
index 2112
t -NONE-
index 2113
t VBG
index 2114
t DT
index 2115
t NN
index 2116
t POS
index 2117
t JJ
index 2118
t NN
index 2119
t ,
index 2120
t VBG
index 2121
t TO
index 2122
t NN
index 2123
t NNS
index 2124
t VBD
index 2125
t -NONE-
index 2126
t NNP
index 2127
t .
index 2128
t JJ
index 2129
t NNS
index 2130
t IN
index 2131
t DT
index 2132
t NNP
index 2133
t CC
index 2134
t NNP
index 2135
t NNP
index 2136
t VBD
index 2137
t DT
index 21

t JJ
index 2680
t IN
index 2681
t NNS
index 2682
t CC
index 2683
t NNS
index 2684
t .
index 2685
t RB
index 2686
t ,
index 2687
t NN
index 2688
t IN
index 2689
t DT
index 2690
t JJ
index 2691
t CD
index 2692
t NNS
index 2693
t VBD
index 2694
t NN
index 2695
t NNS
index 2696
t RB
index 2697
t .
index 2698
t VBG
index 2699
t TO
index 2700
t NNP
index 2701
t NNP
index 2702
t IN
index 2703
t NNP
index 2704
t ,
index 2705
t NNP
index 2706
t ,
index 2707
t DT
index 2708
t JJS
index 2709
t RB
index 2710
t ,
index 2711
t VBD
index 2712
t JJ
index 2713
t NN
index 2714
t IN
index 2715
t CD
index 2716
t ,
index 2717
t DT
index 2718
t NN
index 2719
t IN
index 2720
t CD
index 2721
t NN
index 2722
t .
index 2723
t NNP
index 2724
t POS
index 2725
t NN
index 2726
t IN
index 2727
t DT
index 2728
t JJ
index 2729
t CD
index 2730
t NNS
index 2731
t IN
index 2732
t CD
index 2733
t VBD
index 2734
t CD
index 2735
t ,
index 2736
t -NONE-
index 2737
t JJ
index 2738
t IN
index 2739
t DT
index 2740
t JJ
index 27

...

index 97632
t IN
index 97633
t JJS
index 97634
t CD
index 97635
t NNS
index 97636
t VBP
index 97637
t NNS
index 97638
t NNS
index 97639
t IN
index 97640
t DT
index 97641
t JJ
index 97642
t CD
index 97643
t NNS
index 97644
t -NONE-
index 97645
t .
index 97646
t RB
index 97647
t ,
index 97648
t JJ
index 97649
t NN
index 97650
t VBZ
index 97651
t VBN
index 97652
t -NONE-
index 97653
t IN
index 97654
t DT
index 97655
t JJ
index 97656
t NN
index 97657
t .
index 97658
t NNP
index 97659
t NNP
index 97660
t NNP
index 97661
t VBD
index 97662
t -NONE-
index 97663
t PRP
index 97664
t VBD
index 97665
t PRP$
index 97666
t $
index 97667
t CD
index 97668
t CD
index 97669
t -NONE-
index 97670
t JJ
index 97671
t NN
index 97672
t IN
index 97673
t RB
index 97674
t VBN
index 97675
t NNP
index 97676
t NNP
index 97677
t NNP
index 97678
t ,
index 97679
t DT
index 97680
t NNP
index 97681
t NN
index 97682
t VBG
index 97683
t NN
index 97684
t .
index 97685
t DT
index 97686
t NN
index 97687
t JJ
index 97688
t NN

index 98262
t DT
index 98263
t NN
index 98264
t VBZ
index 98265
t VBN
index 98266
t NNS
index 98267
t TO
index 98268
t VB
index 98269
t DT
index 98270
t NNS
index 98271
t VBN
index 98272
t -NONE-
index 98273
t IN
index 98274
t DT
index 98275
t CD
index 98276
t NN
index 98277
t .
index 98278
t IN
index 98279
t DT
index 98280
t NN
index 98281
t VBG
index 98282
t IN
index 98283
t ,
index 98284
t RB
index 98285
t ,
index 98286
t DT
index 98287
t NNS
index 98288
t VBP
index 98289
t VBG
index 98290
t IN
index 98291
t NNS
index 98292
t MD
index 98293
t VB
index 98294
t IN
index 98295
t DT
index 98296
t NNS
index 98297
t IN
index 98298
t NNP
index 98299
t NNS
index 98300
t VBP
index 98301
t -NONE-
index 98302
t TO
index 98303
t VB
index 98304
t DT
index 98305
t NN
index 98306
t -NONE-
index 98307
t PRP
index 98308
t VBP
index 98309
t VBN
index 98310
t -NONE-
index 98311
t TO
index 98312
t VB
index 98313
t -NONE-
index 98314
t .
index 98315
t NNS
index 98316
t VBP
index 98317
t IN
index 98318
t

index 99012
t NN
index 99013
t VBD
index 99014
t CD
index 99015
t NNS
index 99016
t DT
index 99017
t NN
index 99018
t TO
index 99019
t $
index 99020
t CD
index 99021
t -NONE-
index 99022
t .
index 99023
t IN
index 99024
t NNP
index 99025
t ,
index 99026
t NNS
index 99027
t IN
index 99028
t CD
index 99029
t NN
index 99030
t NNS
index 99031
t ,
index 99032
t NNP
index 99033
t NNP
index 99034
t CC
index 99035
t NNP
index 99036
t NNP
index 99037
t ,
index 99038
t WDT
index 99039
t -NONE-
index 99040
t VBP
index 99041
t TO
index 99042
t DT
index 99043
t JJ
index 99044
t NNP
index 99045
t NNP
index 99046
t ,
index 99047
t NN
index 99048
t VBD
index 99049
t -NONE-
index 99050
t TO
index 99051
t VB
index 99052
t DT
index 99053
t JJ
index 99054
t NN
index 99055
t NN
index 99056
t ,
index 99057
t DT
index 99058
t NN
index 99059
t VBD
index 99060
t -NONE-
index 99061
t -NONE-
index 99062
t .
index 99063
t NNS
index 99064
t IN
index 99065
t DT
index 99066
t NN
index 99067
t ,
index 99068
t DT
inde

t ,
index 99762
t IN
index 99763
t DT
index 99764
t VBN
index 99765
t NNS
index 99766
t VBD
index 99767
t NNS
index 99768
t IN
index 99769
t DT
index 99770
t NNS
index 99771
t WP
index 99772
t -NONE-
index 99773
t VBD
index 99774
t RB
index 99775
t VBN
index 99776
t RB
index 99777
t JJ
index 99778
t DT
index 99779
t NN
index 99780
t IN
index 99781
t NN
index 99782
t NNS
index 99783
t .
index 99784
t DT
index 99785
t NN
index 99786
t IN
index 99787
t DT
index 99788
t NN
index 99789
t POS
index 99790
t NN
index 99791
t MD
index 99792
t RB
index 99793
t VB
index 99794
t DT
index 99795
t NN
index 99796
t IN
index 99797
t NNP
index 99798
t POS
index 99799
t NN
index 99800
t NN
index 99801
t VBD
index 99802
t RBR
index 99803
t IN
index 99804
t DT
index 99805
t JJ
index 99806
t NNS
index 99807
t POS
index 99808
t .
index 99809
t NNP
index 99810
t NNP
index 99811
t ,
index 99812
t DT
index 99813
t NN
index 99814
t IN
index 99815
t NNP
index 99816
t NNP
index 99817
t NNP
index 99818
t NNPS
inde

t JJ
index 100512
t NNS
index 100513
t .
index 100514
t RB
index 100515
t ,
index 100516
t PRP
index 100517
t VBD
index 100518
t -NONE-
index 100519
t DT
index 100520
t JJ
index 100521
t NNS
index 100522
t NN
index 100523
t VBN
index 100524
t -NONE-
index 100525
t CD
index 100526
t NNS
index 100527
t IN
index 100528
t VBD
index 100529
t JJ
index 100530
t JJ
index 100531
t NNS
index 100532
t ,
index 100533
t CC
index 100534
t EX
index 100535
t VBD
index 100536
t DT
index 100537
t NN
index 100538
t IN
index 100539
t DT
index 100540
t JJ
index 100541
t NN
index 100542
t .
index 100543
t PRP
index 100544
t RB
index 100545
t VBD
index 100546
t IN
index 100547
t JJR
index 100548
t IN
index 100549
t DT
index 100550
t NN
index 100551
t NNS
index 100552
t -NONE-
index 100553
t VBP
index 100554
t VBN
index 100555
t IN
index 100556
t JJ
index 100557
t NN
index 100558
t NN
index 100559
t IN
index 100560
t DT
index 100561
t NNP
index 100562
t NNP
index 100563
t ,
index 100564
t CC
index 100565
t ``

In [ ]:
# question: what fraction of adjectives JJ are followed by a noun NN

# create a list of all tags (without the words)
tags = [pair[1] for pair in tagged_words]

# create a list of JJ tags
jj_tags = []

# create a list of (JJ, NN) tags
jj_nn_tags = [(___) for index, t in enumerate(tags) 
              if ___ and ___]

print(len(jj_tags))
print(len(jj_nn_tags))
print(len(jj_nn_tags) / len(jj_tags))

In [ ]:
# question: what fraction of determiners DT are followed by a noun NN
dt_tags = [___]
dt_nn_tags = [(___) for index, t in enumerate(tags) 
              if ___ and ___]

print(len(dt_tags))
print(len(dt_nn_tags))
print(len(dt_nn_tags) / len(dt_tags))

In [ ]:
# question: what fraction of modals MD are followed by a verb VB?
md_tags = [___]
md_vb_tags = [(___) for index, t in enumerate(tags) 
              if ___ and ___]

print(len(md_tags))
print(len(md_vb_tags))
print(len(md_vb_tags) / len(md_tags))